# 1) Simulation with fixed parameters

In [1]:
import os
import sys
module_path = os.path.abspath(os.path.join('../..'))
if module_path not in sys.path:
    sys.path.append(module_path)

In [2]:
from BSDE import * 
import warnings 
import bokeh
from bokeh.layouts import gridplot
from bokeh.plotting import figure, output_notebook, show, output_file
import time
warnings.filterwarnings("ignore")

In [3]:
T = 0.5
K = 100
S0 = 100
sigma = 0.2
r = 0.04
mu = 0.06
R = 0.06
q = 0.

In [77]:
m = 12
N = 1000
l = 1.
deg = 5
n_picard = 3
n_neighbors = np.floor(0.1 * N)
M_run = 1

In [80]:
a = np.zeros(M_run)
timing = np.zeros_like(a)
for i in range (M_run): 
    start = time.time()
    test = BSDE(S0, K, T, mu, sigma, q)
    a[i] = test.get_price_derivative(R, r, N, m, deg=deg, 
                                     n_picard=n_picard, l=0.2, n_neighbors=n_neighbors)
    elapsed = time.time() - start
    timing[i] = round(elapsed, 3)
    print (a[i])

7.77620116716


In [10]:
import pandas as pd

In [11]:
param = ['q', 'mu', 'R ', 'r ','sigma', 'T', 'K', 'S0']
values = [q, mu, R, r, sigma, T, K, S0]
dataset = list(zip(param,values))
df_param = pd.DataFrame(data = dataset, columns=['Parameters', 'values'])

In [12]:
sparam = ['N_particles', 'm_discretization', 'N_run', 'n_picard', 'degree', 'nearest neighbors', 'l']
svalues = [N, m, M_run, n_picard, deg, n_neighbors, l]
sp_dataset = list(zip(sparam,svalues))
df_sparam = pd.DataFrame(sp_dataset, columns=['Specific Parameters', 'values'])
df_sparam

Specific Parameters  values
0         N_particles  1000.0
1    m_discretization    12.0
2               N_run    20.0
3            n_picard     3.0
4              degree     5.0
5   nearest neighbors   100.0
6                   l     1.0

In [13]:
run_id = ["run {}".format(i) for i in range(1, M_run+1)]
df = pd.DataFrame(list(zip(run_id, a, timing)), columns = ['run','values', 'time'])

In [14]:
min_a = round(df['values'].min(), 4)
max_a = round(df['values'].max(), 4)
mean_a = round(df['values'].mean(), 4)
std_a = round(df['values'].std(), 4)
left = round(mean_a - 1.96 * std_a / M_run, 4)
right = round(mean_a + 1.96 * std_a / M_run, 4)

In [15]:
stat_param = ['mean', 'std', '95% confidence interval', 'min', 'max']
stat_values = [mean_a, std_a, [left, right], min_a, max_a]
stat_data = list(zip(stat_param, stat_values))
stat_df = pd.DataFrame(stat_data, columns = ['stat parameter', 'values'])
stat_df

stat parameter            values
0                     mean            7.1779
1                      std            0.3088
2  95% confidence interval  [7.1476, 7.2082]
3                      min            6.7418
4                      max            7.7752

In [16]:
df_join = pd.concat([df_param, df_sparam, df, stat_df], axis = 0)
df_join.to_csv('output_derivative.csv')

# 2) Impact of number of Nearest Neighbors

In [65]:
price_nn = np.zeros(len(list(range(1, N, 50))))
timing_nn = np.zeros_like(price_nn)
for i, n_neighbors_i in enumerate(list(range(1, N, 50))):
    start = time.time()
    for __ in range (5): 
        test = BSDE(S0, K, T, mu, sigma, q)
        price_nn[i] = price_nn[i] + test.get_price_derivative(R, r, N, m, l=1., n_neighbors=n_neighbors_i,
                                                     use_display=False) /5
    print (price_nn[i])
    elapsed = time.time() - start
    timing_nn[i] = round(elapsed, 2)

7.02982787877
7.17584846595
7.1897480934
7.27751895209
6.97402817925
7.40053066506
7.42635377649
7.29865876421
7.53737591621
7.47443458707
7.54601093695
7.30598611121
7.505140511
7.48107685181
7.27042844091
7.54161059057
7.45131586794
7.27230992898
7.56275491661
7.58226700777


In [90]:
output_notebook()
price_nn_2 = np.array([7.26098091582,
7.25547347254,
7.20359139458,
7.29538479982,
7.25950621811,
7.31272465784,
7.33276085992,
7.30376850493,
7.27789437833,
7.4311556616,
7.35043095794,
7.44472882184,
7.38451458176,
7.31696191183,
7.30073820504,
7.2745254987,
7.27377147996,
7.28211668548,
7.5433479537,
7.3681803583])
p = figure(width=400, plot_height=400, title='Price against number of neighbors with N_particles = {}'.format(N))
p.circle(list(range(1, N, 50)), price_nn_2, color='navy')
show(p)

Loading BokehJS ...

# 3) Impact of parameter l 

In [66]:
price_l = np.zeros(len(list(range(1, 200, 4))))
for i, l_i in enumerate(list(range(1, 200, 4))):
    for __ in range(5): 
        test = BSDE(S0, K, T, mu, sigma, q)
        price_l[i] = price_l[i] + test.get_price_derivative(R, r, 1000, 
                                                            4, l=l_i, n_neighbors=100, n_picard = 2, 
                                                            use_display=False) / 5
    print (price_l[i])

7.4825948185
7.35404869472
7.16635972543
7.1907041917
7.20510198515
7.13145838054
7.35393874549
7.08844043599
7.32713908102
7.07605761716
7.2469645513
7.32248552776
7.18077756676
6.98461115799
7.35269621891
7.26922601427
7.16455842955
7.24116775004
7.1939668795
7.10656062356
7.17688223907
7.55886211899
7.48520829922
7.26507303732
7.1513265091
7.2088708633
7.05077494283
7.2896671765
7.30149642306
7.267854037
7.19906845789
7.1280449771
7.32470193773
7.21914309474
7.12395692069
7.24177612459
7.13973265782
7.37683007305
7.5290934254
7.35125616139
7.05346272001
7.28678714441
7.25570879165
7.12014015907
6.87517876206
7.42596142804
7.2575734469
7.18708918479
6.9349470037
7.28645461608


In [81]:
price_ll = np.zeros(10)
range_l = [0.1 * x for x in range(1, 11)]
for i, l_i in enumerate(range_l):
    for __ in range(5): 
        test = BSDE(S0, K, T, mu, sigma, q)
        price_ll[i] = price_l[i] + test.get_price_derivative(R, r, 1000, 
                                                            4, l=l_i, n_neighbors=100, n_picard = 2, 
                                                            use_display=False) / 5
    print (price_l[i])

7.4825948185
7.35404869472
7.16635972543
7.1907041917
7.20510198515
7.13145838054
7.35393874549
7.08844043599
7.32713908102
7.07605761716


array([ 9.09387052,  8.85724215,  8.67929484,  8.74884348,  8.69368298,
        8.50910913,  8.81303968,  8.51588889,  8.81197861,  8.489089  ,
        7.48259482,  7.35404869,  7.16635973,  7.19070419,  7.20510199,
        7.13145838,  7.35393875,  7.08844044,  7.32713908,  7.07605762,
        7.24696455,  7.32248553,  7.18077757,  6.98461116,  7.35269622,
        7.26922601,  7.16455843,  7.24116775,  7.19396688,  7.10656062,
        7.17688224,  7.55886212,  7.4852083 ,  7.26507304,  7.15132651,
        7.20887086,  7.05077494,  7.28966718,  7.30149642,  7.26785404,
        7.19906846,  7.12804498,  7.32470194,  7.21914309,  7.12395692,
        7.24177612,  7.13973266,  7.37683007,  7.52909343,  7.35125616,
        7.05346272,  7.28678714,  7.25570879,  7.12014016,  6.87517876,
        7.42596143,  7.25757345,  7.18708918,  6.934947  ,  7.28645462])

In [85]:
price_ll

array([ 9.09387052,  8.85724215,  8.67929484,  8.74884348,  8.69368298,
        8.50910913,  8.81303968,  8.51588889,  8.81197861,  8.489089  ])

In [86]:
output_notebook()
p = figure(width=400, plot_height=400, title='Price against parameter l')
p.circle(range_l + list(range(1, 200, 4)), np.concatenate((price_ll, price_l), axis=0), color='navy')
show(p)

Loading BokehJS ...

# 4) Plotting Z against Stocks Input

In [26]:
output_notebook()
T = 0.5
m_time_discretization = 12
K = 100
S0 = 100
sigma = 0.2
r = 0.04
N_particles = 10000
n_neighbors = 999
mu = 0.06
R = 0.06
q = 0.
test = BSDE(S0, K, T, mu, sigma, q)
price_derivative = test.get_price_derivative(R, r, N_particles, m_time_discretization, l=1., 
                                             n_neighbors=n_neighbors,use_display=True)

print (price_derivative)

Loading BokehJS ...

7.33027932205


In [ ]:
T = 1.
K = 100
S0 = 100
sigma = 0.2
r = 0.01
mu = 0.06
R = 0.01
q = 0.

In [ ]:
m = 6
N = 10000
l = 1.
deg = 5
n_picard = 1
n_neighbors = np.floor(0.9 * N)
M_run = 20

In [ ]:
test = BSDE(S0, K, T, mu, sigma, q)
print (test.get_price_derivative(R, r, N, m, deg=deg, 
                          n_picard=n_picard, l=l, n_neighbors=n_neighbors, 
                          oPayoff = "call average"))

In [75]:
output_notebook()
p = figure(width=400, plot_height=400, title='Time against number of NN compared to N_log_N behaviour')
p.multi_line([list(range(1, N, 50)), list(range(1, N, 50))],
             [timing_nn / 5,0.5 / 12 * n_log_n], 
             color=['red','green'])
show(p)


Loading BokehJS ...

In [51]:
expected_time_func = lambda x : x * np.log(x)
n_log_n = expected_time_func(list(range(1, N, 50)))
square_func = lambda x : np.square(x)

In [30]:
n_log_n

array([    0.        ,   200.52310727,   466.1271722 ,   757.60925536,
        1065.96428652,  1386.88868772,  1717.84018969,  2057.13596444,
        2403.57853235,  2756.27177012,  3114.51965664,  3477.76587984,
        3845.55555566,  4217.50977708,  4593.30802881,  4972.67564447,
        5355.3746186 ,  5741.19672142,  6129.95823711,  6521.49587348])

In [45]:
3 * np.log(3)

3.2958368660043291

In [70]:
N_squared = square_func(list(range(1, N, 50)))